## 作业三：爬取教授信息并结构化处理（完整爬取）

针对之前定义模板导致有些教授不匹配的情况，现对作业进行如下几点改进：
1.先对网页信息进行定位并清理，并删除诸如“姓名”、“职务”等关键字中的空格以保证后续提取不会出错；
2.由于桂荷发教授没有科研成果，所以对其网页进行一个判断并为其单独设计；
3.由于蒋崇辉教授的邮箱部分为联系方式，故也对其网页进行判断并单独设计。

### 代码如下：

In [7]:
import requests
import re
import pandas as pd

url1="http://finance.jxufe.edu.cn/news-list-jiaoshou-1.html"
url2="http://finance.jxufe.edu.cn/news-list-jiaoshou-2.html"

def get_teachers_href(url):
    r=requests.get(url)
    html_text=r.text
    html=re.findall(r'<div class="pic"> <a href="(.*?)"><img style="width:130px;height:160px;" src=".*?"></a></div>',html_text)
    return html
    
links1 = get_teachers_href(url1)
links2 = get_teachers_href(url2)
links = links1 + links2
del links1
del links2

url = 'http://finance.jxufe.edu.cn/news-show-1366.html'
def get_info(url):
    r = requests.get(url)
    html_text = r.text
    start = html_text.find('<div class="ne_main_R">')
    end = html_text.find('<div class="ne_main_f">')
    context = html_text[start:end]
    p = re.compile('<.*?>')
    context = p.sub('',context)
    p2 = re.compile('&nbsp;')
    context = p2.sub('',context)
    p3 = re.compile('　　')
    context = p3.sub('',context)
    p4 = re.compile('   ')
    context = p4.sub('',context)    
    if url != "http://finance.jxufe.edu.cn/news-show-1380.html":
        info = re.search(r'姓名：(.*?)性别：(.*?)出生年月：(.*?)政治面貌：(.*?)毕业院校：(.*?)毕业专业：(.*?)职务：(.*?)职称：(.*?)邮箱(?:：|:)(.*?)自我简介',context)
    else:
        info = re.search(r'​姓名：(.*?)性别：(.*?)出生年月：(.*?)政治面貌：(.*?)毕业院校：(.*?)毕业专业：(.*?)职称：(.*?)职务：(.*?)联系方式：(.*?)​自我简介',context)
    xm = info.group(1)
    xb = info.group(2)
    csny = info.group(3)
    zzmm = info.group(4)
    byyx = info.group(5)
    byzy = info.group(6)
    zw = info.group(7)
    zc = info.group(8)
    yx = info.group(9)
    if url != "http://finance.jxufe.edu.cn/news-show-1363.html":
        pre_zwjj = re.search(r'自我简介(.*?)科研成果',context,re.S)
        zwjj = pre_zwjj.group(1)
        index_kycg = context.find('科研成果')+4
        kycg = context[index_kycg:]
    else:
        pre_zwjj = re.search(r'自我简介(.*?)代表性论文',context,re.S)
        zwjj = pre_zwjj.group(1)
        index_kycg = context.find('代表性论文')+5
        kycg = context[index_kycg:]
    
    teacher_info = {'姓名':xm,
            '性别':xb,
            '出生年月':csny,
            '政治面貌':zzmm,
            '毕业院校':byyx,
            '毕业专业':byzy,
            '职务':zw,
            '职称':zc,
            '邮箱':yx,
            '自我简介':zwjj,
            '科研成果':kycg}
    return(teacher_info)

In [8]:
teacher = []
for i in range(len(links)):
        teacher.append(get_info(links[i]))

In [9]:
df = pd.DataFrame.from_dict(teacher)
order = ['姓名','性别','出生年月','政治面貌','毕业院校','毕业专业','职务','职称','邮箱','自我简介','科研成果']
df = df[order] 

In [10]:
df

姓名 性别     出生年月  政治面貌         毕业院校             毕业专业          职务  \
0    曹邓  女           中共党员       江西财经大学              管理学        系副主任   
1   陈春霞  女             群众       江西财经大学              金融学               
2   陈家洪  男           中共党员       江西财经大学     经济统计（证券研究方向）               
3   桂荷发  男           民进会员       中国人民大学              金融学          院长   
4   黄飞鸣  男           民革党员         厦门大学              金融学               
5   胡援成  男           中共党员         厦门大学              金融学        中心主任   
6   吕江林  男           中共党员       中南财经大学              经济学  应用金融研究中心主任   
7   刘兴华  男           中共党员         厦门大学             世界经济         副院长   
8   凌爱凡  男           中共党员       西安交通大学             计算数学               
9   彭玉镏  男  1973年3月  中共党员       上海财经大学              金融学               
10  蒋崇辉  男   1980.9  中共党员       电子科技大学  管理科学与工程（金融工程方向）          教授   
11  孙爱琳  女           中共党员         浙江大学            政治经济学               
12  王 辉              中共党员       江西财经大学              财政学               
13   汪洋  男           中共党员       上海财经大学              金融学               
14   肖峻  男             民进  同济大学经济与管理学院            管理学博士         副院长   
15  杨玉凤  女           民主党派       江西财经大学              金融学               
16   杨荣  女           中共党员       江西财经大学              金融学               
17   严武  男             党员       江西财经大学              经济学               

                      职称                     邮箱  \
0                     教授   laotoutou@aliyun.com   
1                  教授/硕导        new9360@163.com   
2                  教授/硕导         jxmcjh@126.com   
3                     教授       guihefa@163.com​   
4               教授/硕士生导师       172348582@qq.com   
5                  教授/博导          hu-yc@163.com   
6                 教授/博导​        ljl5983@126.com   
7                  教授/博导        lxh7572@126.com   
8                  教授/博导       aiffling@163.com   
9   教授/博导联系电话：83816792电子     pengyuliu@sohu.com   
10         金融工程系主任，博士生导师        jch0920@163.com   
11                 教授、硕导        sal6660@126.com   
12                 教授/硕导         wh6660@126.com   
13                 教授/博导  wangyang@jxufe.edu.cn   
14                 教授/博导    xiao_jun913@163.com   
15                 教授/硕导      xialuoren@126.com   
16                 教授、硕导   yonghongyang@163.com   
17                   教授​       923108620@qq.com   

                                                 自我简介  \
0   一、开设课程：保险学原理、财产保险、保险中介管理、保险实务研究、商业保险理论与研究、财产保险...   
1   开设课程本科生主讲的主要课程有：《货币银行学》、《国际金融》《金融企业会计》、《投资项目评估...   
2       一、开设课程：证券投资学、证券投资基金、投资管理、创业投资管理、私募股权投资、证券投资分析   
3   桂荷发，1968年9月出生，江西余江人，经济学博士、教授、博士生导师，。毕业于中国人民大学财...   
4   黄飞鸣，河南永城人，经济学博士，现系江西财经大学金融学院教授、博士生导师，江西省高校中青年骨...   
5   一、开设课程：本科：国际金融管理；硕士研究生：公司金融；博士研究生：公司金融理论与政策，外文...   
6   一、开设课程本科生课程:货币银行学、国际金融、证券投资学、商业银行经营管理学、金融工程硕士生...   
7   一、开设课程系统讲授《国际金融》、《国际货币与金融经济学》、《货币银行学》、《中央银行学》等...   
8   一、基本情况 凌爱凡：江西财经大学金融学首席教授，博士生导师，江西财经大学金融科技与监管研究...   
9   开设课程宏观审慎监管理论与政策（博士课程）、金融监管（硕士课程）、国际金融、金融机构风险管理...   
10  1.教育和培训经历2014.5-2015.4：加拿大/温莎大学Odette商学院（访问学者）...   
11  一、开设课程本科生：货币银行学、财政学、预算会计、保险学、保险会计、社会保障学等。研究生：金...   
12  一、开设课程本科生：“保险学”；“人身保险”；“责任保险”；“保险经营管理”；“保险营销学”...   
13  一、开设课程：本科：《国际金融》，《国际货币与金融经济学》，《中央银行学》；硕士研究生：《国...   
14  一、从业经历与学术简历 同济大学博士、民进财大副主委，现任金融管理国际研究院副院长、教授、博...   
15  一、开设课程 主要有《国际金融》、《国际金融实务》、《货币银行学》等课程。二、获得奖励199...   
16      一、开设课程：货币银行学、商业银行学、二、获得奖励：略三、社会兼职：江西省货币学会常务理事   
17  简介： 严武，现任江西财经大学金融学教授（国家二级）、博士生导师，江西财经大学金融研究所所长...   

                                                 科研成果  
0   一、论文1.“WTO:中国民族保险业的机遇与挑战”，独著，《理论导报》2000年第9期。2....  
1   一、论文1、《我国国债与企业债券的比较》，独著，《江西财经大学学报》2006年第9月期（人大...  
2   一、论文1. “从股票市场角度看收入分配不公问题”，独著，《华东经济管理》2011年第8期。...  
3   1.桂荷发，科技金融统计研究，获2013年全国首届科技金融征文一等奖。2.桂荷发、蔡明超、石...  
4   ：（一）学术论文（发表学术论文60余篇，代表性论文有：1.Huang Feiming.Emp...  
5   一、论文1、“地价模型初探”，独著，数量经济与技术经济研究 1990年第6期。2、“商业银行...  
6   主要科研成果一、论文1、《具有联合椭圆不确定集与概率约束的鲁棒投资组合选择》，《控制与决策》...  
7   一、论文1.“日本银行对日元汇率的干预：基于动态博弈的分析”，第一作者，《现代日本经济》20...  
8   英文期刊论文[15] AifanLing（凌爱凡），Jie Sun，Meihua Wang，...  
9   一、论文1.“人民币外汇市场压力及其影响因素研究——基于LT-TVP-VA